# Utilización del servicio de alquiler de bicicletas en Toronto en el año 2018

### Disponible en Kaggle en el siguiente enlace (que NO debe usarse para el ejercicio, sino los CSV que se adjuntaron al email):
https://www.kaggle.com/jackywang529/toronto-bikeshare-data


El propósito de este análisis es utilizar los conjuntos de datos trimestrales del año 2018 de la empresa de alquiler de bicicletas en Toronto. Se trata de *cuatro* conjuntos de datos separados, que incluyen entre 178.559 y 822.536 observaciones, siempre con nueve variables. Cada fila representa un viaje realizado.

### Variables y significado

Las variables utilizadas para describir cada viaje son:

* trip_id – identificador global del viaje
* trip_duration_seconds – duración del viaje en segundos
* from_station_id – identificador numérico de la estación de origen
* trip_start_time – instante (timestamp) en el que se inició el viaje
* from_station_name – nombre de la intersección más cercana a la estación origen
* trip_stop_time – instante (timestamp) en el que finalizó el viaje
* to_station_id – identificador numérico de la estación de destino
* to_station_name – nombre de la intersección más cercana a la estación de destino
* user_type – tipo de usuario (indicador binario): miembro registrado con cuota anual / usuario ocasional no registrado

**Nombre completo del alumno:**  

# INSTRUCCIONES

En cada celda debes responder a la pregunta formulada, asegurándote de que el resultado queda guardado en la(s) variable(s) que por defecto vienen inicializadas a `None`. No se necesita usar variables intermedias, pero puedes hacerlo siempre que el resultado final del cálculo quede guardado exactamente en la variable que venía inicializada a None (debes reemplazar None por la secuencia de transformaciones necesarias, pero nunca cambiar el nombre de esa variable). 

**No olvides borrar la línea *raise NotImplementedError()* de cada celda cuando hayas completado la solución de esa celda y quieras probarla**.

Después de cada celda evaluable verás una celda con código. Ejecútala (no modifiques su código) y te dirá si tu solución es correcta o no. En caso de ser correcta, se ejecutará correctamente y no mostrará nada, pero si no lo es mostrará un error. Además de esas pruebas, se realizarán algunas más (ocultas) a la hora de puntuar el ejercicio, pero evaluar dicha celda es un indicador bastante fiable acerca de si realmente has implementado la solución correcta o no. Asegúrate de que, al menos, todas las celdas indican que el código es correcto antes de enviar el notebook terminado.


**Nunca se debe redondear ninguna cantidad si no lo pide explícitamente el enunciado**

### Cada solución debe escribirse obligatoriamente en la celda habilitada para ello. Cualquier celda adicional que se haya creado durante el desarrollo deberá ser eliminada.

Si necesitas crear celdas auxiliares durante el desarrollo, puedes hacerlo pero debes asegurarte de borrarlas antes de entregar el notebook.

### Sobre los cuatro datasets anteriores (Bike Share Toronto Ridership_Q1 2018.csv hasta Q4) se pide:

**(1 punto)** Ejercicio 1

* Leer por separado cada uno de ellos (sin cachear), tratando de que Spark infiera el tipo de dato de cada columna, y **unirlos en un solo DF** que tampoco debe ser cacheada todavía, ya que en el siguiente paso aún realizaremos otro pre-procesamiento.
* Los cuatro contienen las mismas columnas por lo que no habrá problemas para utilizar la operación `union` encadenada tres veces para crear el DF final.

In [0]:
# LÍNEA EVALUABLE, NO RENOMBRAR LAS VARIABLES
tripsQ1 = None # Primer CSV
tripsQ2 = None # Segundo CSV
tripsQ3 = None # Tercer CSV
tripsQ4 = None # Cuarto CSV
tripsTorontoRawDF = None # Unión de todos

# YOUR CODE HERE
tripsQ1 = spark.read.option("header", "true")\
                 .option("inferSchema", "true")\
                 .csv("abfss://datos@masterjdub.dfs.core.windows.net/Bike Share Toronto Ridership_Q1 2018.csv")

tripsQ2 = spark.read.option("header", "true")\
                 .option("inferSchema", "true")\
                 .csv("abfss://datos@masterjdub.dfs.core.windows.net/Bike Share Toronto Ridership_Q2 2018.csv")
tripsQ3 = spark.read.option("header", "true")\
                 .option("inferSchema", "true")\
                 .csv("abfss://datos@masterjdub.dfs.core.windows.net/Bike Share Toronto Ridership_Q3 2018.csv")
tripsQ4 = spark.read.option("header", "true")\
                 .option("inferSchema", "true")\
                 .csv("abfss://datos@masterjdub.dfs.core.windows.net/Bike Share Toronto Ridership_Q4 2018.csv")

tripsTorontoRawDF = tripsQ1.union(tripsQ2).union(tripsQ3).union(tripsQ4)

In [0]:
from pyspark.sql.types import DoubleType
assert(tripsTorontoRawDF.count() == 1922955)

**(1 punto)** Ejercicio 2

* Las columnas `trip_start_time` y `trip_stop_time` son en realidad instantes de tiempo que Spark debería procesar como timestamp. Reemplaza **ambas columnas** por su versión convertida a timestamp, utilizando `withColumn` y donde el nuevo valor de la columna viene dado por el siguiente código:
        F.from_unixtime(F.unix_timestamp('nombreColumna', 'M/d/yyyy H:mm')).cast("timestamp"))
El DF resultante debe ser almacenado en la variable `tripsTorontoDF`.


In [0]:
# No olvides los imports que necesites...
# LÍNEAS EVALUABLES, NO RENOMBRAR LAS VARIABLES
tripsTorontoDF = None
# YOUR CODE HERE

from pyspark.sql import functions as F
tripsTorontoDF = tripsTorontoRawDF\
                                    .withColumn("trip_start_time",\
                                              F.from_unixtime(F.unix_timestamp('trip_start_time', 'M/d/yyyy H:mm')).cast("timestamp"))\
                                    .withColumn("trip_stop_time",\
                                              F.from_unixtime(F.unix_timestamp('trip_stop_time', 'M/d/yyyy H:mm')).cast("timestamp"))


In [0]:
typesDict = dict(tripsTorontoDF.dtypes)
assert(typesDict["trip_start_time"] == "timestamp") 
assert(typesDict["trip_stop_time"] == "timestamp") 

**(1 punto)** Ejercicio 3

* Primero, debemos quedarnos solamente con las filas donde `trip_start_time` no sea null.
* Sobre el DF resultado de lo anterior, añadir una columna adicional **Mes** y con el mes representado en **trip_start_time**. Dicha columna será de tipo entero y se puede obtener usando `withColumn` con la función `F.month("colName")`, que recibe un nombre de columna y devuelve un objeto columna de enteros que van de 1 a 12. 
* Encadenar esta transformación con otra en la que la columna **Mes** sea reemplazada por su traducción a  cadena de caracteres de 3 letras, siendo la correspondencia 1: Ene, 2: Feb, 3: Mar, 4: Abr, 5: May, 6: Jun, 7: Jul, 8: Ago, 9: Sep, 10: Oct, 11: Nov, 12: Dic.
* Finalmente, añadir una nueva columna **Hora** que contenga la hora de inicio del viaje, aplicando `withColumn` con la función `F.hour("colName")` que recibe un nombre de columna y recibe un objeto columna de enteros de 0 a 23.
* El DF resultante de todas estas transformaciones debe guardarse en la variable `tripsTorontoTimesDF`, que por tanto tendrá 2 columnas más que el DF original `tripsTorontoDF`, y que debe quedar **cacheado**.

In [0]:
# LÍNEA EVALUABLE, NO RENOMBRAR VARIABLES
# imports......
tripsTorontoTimesDF = None
# YOUR CODE HERE

from itertools import chain

equivalencias = {
    1: 'Ene', 
    2: 'Feb',
    3: 'Mar',
    4: 'Abr',
    5: 'May',
    6: 'Jun',
    7: 'Jul',
    8: 'Ago',
    9: 'Sep',
    10: 'Oct',
    11: 'Nov',
    12: 'Dic'
}
mapping_expr = F.create_map([F.lit(x) for x in chain(*equivalencias.items())])

tripsTorontoTimesDF = tripsTorontoDF\
                                    .where(F.col("trip_start_time").isNotNull())\
                                    .withColumn("Mes",F.month("trip_start_time"))\
                                    .withColumn("Mes", mapping_expr.getItem(F.col("Mes")))\
                                    .withColumn("Hora",F.hour("trip_start_time"))
tripsTorontoTimesDF.display()

/databricks/spark/python/pyspark/sql/column.py:477: FutureWarning: A column as 'key' in getItem is deprecated as of Spark 3.0, and will not be supported in the future release. Use `column[key]` or `column.key` syntax instead.
  warnings.warn(


trip_id trip_duration_seconds from_station_id trip_start_time from_station_name trip_stop_time to_station_id to_station_name user_type Mes Hora 2383648 393 7018 2018-01-01T00:47:00Z Bremner Blvd / Rees St 2018-01-01T00:54:00Z 7176 Bathurst St / Fort York Blvd Annual Member Ene 0 2383649 625 7184 2018-01-01T00:52:00Z Ossington Ave / College St 2018-01-01T01:03:00Z 7191 Central Tech (Harbord St) Annual Member Ene 0 2383650 233 7235 2018-01-01T00:55:00Z Bay St / College St (West Side) - SMART 2018-01-01T00:59:00Z 7021 Bay St / Albert St Annual Member Ene 0 2383651 1138 7202 2018-01-01T00:57:00Z Queen St W / York St (City Hall) 2018-01-01T01:16:00Z 7020 Phoebe St / Spadina Ave Annual Member Ene 0 2383652 703 7004 2018-01-01T01:00:00Z University Ave / Elm St 2018-01-01T01:12:00Z 7060 Princess St / Adelaide St E Annual Member Ene 1 2383653 1026 7078 2018-01-01T01:07:00Z College St / Major St 2018-01-01T01:24:00Z 7130 Pears Av / Avenue Rd Annual Member Ene 1 2383654 274 7021 2018-01-01T01:33:00Z Bay St / Albert St 2018-01-01T01:38:00Z 7033 Union Station Annual Member Ene 1 2383655 764 7046 2018-01-01T01:34:00Z Niagara St / Richmond St W 2018-01-01T01:47:00Z 7275 Queen St W / James St Annual Member Ene 1 2383657 237 7044 2018-01-01T01:37:00Z Church St / Alexander St 2018-01-01T01:41:00Z 7028 Gould St / Mutual St Annual Member Ene 1 2383658 180 7198 2018-01-01T01:38:00Z Queen St W / Cowan Ave 2018-01-01T01:41:00Z 7193 Queen St W / Gladstone Ave Annual Member Ene 1 2383659 957 7061 2018-01-01T01:39:00Z Dalton Rd / Bloor St W 2018-01-01T01:55:00Z 7002 St. George St / Bloor St W Annual Member Ene 1 2383660 898 7177 2018-01-01T01:39:00Z East Liberty St / Pirandello St 2018-01-01T01:54:00Z 7206 Claremont St / Dundas St W Annual Member Ene 1 2383661 1529 7107 2018-01-01T01:49:00Z Cherry St / Distillery Ln 2018-01-01T02:14:00Z 7211 Fort York Blvd / Garrison Rd Annual Member Ene 1 2383662 253 7078 2018-01-01T01:57:00Z College St / Major St 2018-01-01T02:01:00Z 7195 Ulster St / Bathurst St Annual Member Ene 1 2383663 348 7095 2018-01-01T02:06:00Z Danforth Ave / Ellerbeck St 2018-01-01T02:11:00Z 7117 Castle Frank Station Annual Member Ene 2 2383664 797 7160 2018-01-01T02:25:00Z King St W / Tecumseth St 2018-01-01T02:38:00Z 7136 Queen St W / Close Ave Casual Member Ene 2 2383665 352 7140 2018-01-01T02:29:00Z Macpherson Ave / Spadina Rd 2018-01-01T02:35:00Z 7003 Madison Ave / Bloor St W Annual Member Ene 2 2383666 382 7149 2018-01-01T02:30:00Z Yarmouth Rd / Christie St 2018-01-01T02:36:00Z 7153 Bloor St W / Christie St Annual Member Ene 2 2383667 433 7111 2018-01-01T02:45:00Z King St W / Douro St 2018-01-01T02:52:00Z 7176 Bathurst St / Fort York Blvd Annual Member Ene 2 2383668 589 7067 2018-01-01T02:53:00Z Yonge St / Harbour St 2018-01-01T03:03:00Z 7259 Lower Spadina Ave / Lakeshore Blvd Annual Member Ene 2 2383669 846 7103 2018-01-01T03:10:00Z Jimmie Simpson Park (Queen St E) 2018-01-01T03:24:00Z 7118 King St W / Bay St (East Side) Annual Member Ene 3 2383670 259 7135 2018-01-01T03:23:00Z Hanna Ave / Liberty St 2018-01-01T03:28:00Z 7148 King St W / Joe Shuster Way Annual Member Ene 3 2383671 401 7033 2018-01-01T03:25:00Z Union Station 2018-01-01T03:31:00Z 7101 Lower Sherbourne St / The Esplanade Annual Member Ene 3 2383672 821 7153 2018-01-01T03:28:00Z Bloor St W / Christie St 2018-01-01T03:41:00Z 7204 College St / Crawford St Annual Member Ene 3 2383673 555 7078 2018-01-01T03:28:00Z College St / Major St 2018-01-01T03:37:00Z 7044 Church St / Alexander St Annual Member Ene 3 2383674 1102 7055 2018-01-01T03:31:00Z Jarvis St / Carlton St 2018-01-01T03:50:00Z 7017 Widmer St / Adelaide St W Annual Member Ene 3 2383675 239 7211 2018-01-01T03:39:00Z Fort York Blvd / Garrison Rd 2018-01-01T03:43:00Z 7000 Fort York Blvd / Capreol Ct Annual Member Ene 3 2383676 478 7156 2018-01-01T03:43:00Z Salem Ave / Bloor St W 2018-01-01T03:51:00Z 7249 Dovercourt Rd / Harrison St (Green P) - SMART Annual Member Ene 3 2383677 180 7158 2018-01-01T03:44:00Z King St W / S

In [0]:
tripsPerMonth = tripsTorontoTimesDF.groupBy("Mes").count().sort("Mes").collect()
assert(tripsPerMonth[0]["count"] == 94783)
assert(tripsPerMonth[1]["count"] == 281219)
assert(tripsPerMonth[2]["count"] == 83324)
assert(tripsPerMonth[3]["count"] == 43859)
assert(tripsPerMonth[4]["count"] == 49731)
assert(tripsPerMonth[5]["count"] == 286316)
assert(tripsPerMonth[6]["count"] == 250837)
assert((tripsPerMonth[7]["count"] == 84959) | (tripsPerMonth[7]["count"] == 84969))
assert(tripsPerMonth[8]["count"] == 212750)
assert(tripsPerMonth[9]["count"] == 104287)
assert(tripsPerMonth[10]["count"] == 175879)
assert(tripsPerMonth[11]["count"] == 255001)

**(1 punto)** Ejercicio 4

* Partiendo de `tripsTorontoTimesDF`, crear un nuevo DataFrame con **tantas filas como horas tiene el día, y tantas columnas como meses del año** de manera que cada celda indique el **número de viajes** que comenzaron a esa hora en ese mes del año. Guardar el resultado en la variable `tripsPerMonthAndHourDF`, cuyas filas deben quedar ordenadas en base a la hora (de 0 a 23), y cuyas columnas deben estar también ordenadas desde `"Ene"` a `"Dic"`, con `"Hora"` como primera columna.

In [0]:
# LÍNEA EVALUABLE, NO RENOMBRAR VARIABLES
tripsPerMonthAndHourDF = None
# YOUR CODE HERE
tripsPerMonthAndHourDF = tripsTorontoTimesDF \
                                            .groupBy("Hora").pivot("Mes", ["Ene", "Feb", "Mar", "Abr", "May", "Jun", "Jul", "Ago", "Sep", "Oct", "Nov", "Dic"])\
                                            .agg(F.count("*").alias("n"))\
                                            .sort("Hora")
                                            

tripsPerMonthAndHourDF.display()

Hora Ene Feb Mar Abr May Jun Jul Ago Sep Oct Nov Dic 0 425 412 689 770 1913 2859 3418 2912 2623 1419 888 782 1 266 308 434 493 1180 1725 1991 1831 1689 943 637 525 2 201 183 318 374 804 1274 1356 1360 1344 684 442 417 3 91 101 156 130 361 587 646 595 632 245 211 164 4 49 56 133 114 227 463 494 504 467 264 253 187 5 198 226 348 381 627 877 1121 1110 1032 860 569 373 6 603 668 995 1092 2043 2802 3232 3088 2800 2373 1745 1082 7 1742 2011 3303 3436 6626 8209 8978 8146 8130 6217 4286 2914 8 5001 5199 8682 9825 17855 20602 23931 22475 21216 17825 11720 8293 9 3728 3769 6497 6790 12063 14044 16089 14978 14710 12381 8314 6287 10 1975 2017 3557 3624 7830 8641 10195 10306 9873 6935 4100 3634 11 1873 1893 3747 3865 9278 10121 11823 12570 11549 7437 4444 3900 12 2259 2386 4548 4761 11427 12701 14796 15539 14362 9308 5445 4696 13 2117 2334 4379 4878 12117 13189 15492 16393 14755 9089 5296 4908 14 2002 2269 4271 4735 11909 13186 14915 15775 14261 8573 4910 4786 15 2483 2855 4933 5690 13518 14495 16429 16923 16075 9899 5835 5362 16 3936 4482 7333 8475 18306 19759 22815 22772 21378 14895 8682 7146 17 4981 6320 10064 11456 25144 28216 32028 31734 29342 21593 11944 9043 18 3314 4383 7332 8440 19013 22257 25347 25571 22663 16048 8319 6396 19 2147 2556 4556 5487 14104 17638 19146 18937 15996 9865 5228 4046 20 1580 1913 3225 3750 10061 13930 15567 14268 11166 6886 3868 3024 21 1275 1511 2549 2835 7194 10429 12081 10314 8459 5558 3164 2311 22 934 1158 1804 2049 5449 7558 8365 7477 6260 3909 2347 1840 23 679 721 1116 1333 3701 5275 6061 5641 4219 2673 1640 1208

In [0]:
assert(len(tripsPerMonthAndHourDF.columns) == 13)
assert(tripsPerMonthAndHourDF.columns[0] == "Hora")
assert(tripsPerMonthAndHourDF.columns[12] == "Dic")
assert(tripsPerMonthAndHourDF.count() == 24)
todasHoras = tripsPerMonthAndHourDF.collect()
assert((todasHoras[0]["Hora"] == 0) & (todasHoras[0]["Dic"]==782))
assert((todasHoras[23]["Hora"] == 23) & (todasHoras[23]["Dic"]==1208))

**(3 puntos)** Ejercicio 5. 

Partiendo de `tripsTorontoTimesDF` definido anteriormente, añadir las siguientes columnas:

* Primero, tres columnas adicionales llamadas `dur_media`, `dur_min`, `dur_max` que contengan, respectivamente, **la duración media, mínima y máxima de los viajes que parten de esa misma estación de origen (from_station_id) a esa misma hora y en ese mismo mes del año**. Es decir, queremos una columna extra para que podamos tener, junto a cada viaje, información agregada de los viajes similares, entendidos como aquellos que salieron a la misma hora de la misma estación. **No se debe utilizar JOIN sino solo funciones de ventana**.
* A continuación, otra columna adicional `diff_dur_porc` que contenga la diferencia, medida en porcentaje, entre la duración del viaje y la duración media de los viajes similares calculada en el apartado anterior. Dicha diferencia debe calcularse como la resta de la duración del viaje menos la duración media, dividida entre la duración media y multiplicada por 100. El resultado debe obtenerse aplicando operaciones aritméticas con columnas existentes, **sin utilizar `when`**.
* El DF resultante con las 4 columnas nuevas que hemos añadido debe almacenarse en la variable `tripsTorontoExtraInfoDF`.

In [0]:
# LÍNEA EVALUABLE, NO RENOMBRAR VARIABLES
# imports necesarios..........
from pyspark.sql import Window
from pyspark.sql import functions as F
window = Window().partitionBy("from_station_id", "Hora", "Mes")

##
windowHoraMesEstacion = None
tripsTorontoExtraInfoDF = None
# YOUR CODE HERE
windowHoraMesEstacion = tripsTorontoTimesDF.withColumn("dur_media", F.mean("trip_duration_seconds").over(window))\
                        .withColumn("dur_max", F.max("trip_duration_seconds").over(window))\
                        .withColumn("dur_min", F.min("trip_duration_seconds").over(window))\

tripsTorontoExtraInfoDF = windowHoraMesEstacion.withColumn("diff_dur_porc", (((F.col("trip_duration_seconds")-F.col("dur_media"))/F.col("dur_media"))*100))


In [0]:
r = tripsTorontoExtraInfoDF.where("trip_id = '2970611'").head()
assert(r.dur_media - 783.366666667 < 0.001)
assert(r.diff_dur_porc - 44.24918088591975 < 0.001)
assert(r.dur_min == 167)
assert(r.dur_max == 2333)

**(3 puntos)** Ejercicio 6

* Partiendo de `tripsTorontoTimesDF`, crear un **grafo** llamado `bikeGraph` utilizando como identificador de los vértices los identificadores de las estaciones. Construye primero un DF con todos los identificadores de las estaciones, simplemente seleccionando **from_station_id**, renombrando adecuadamente el nombre de columna. Puedes almacenar este DF en la variable `verticesDF`. También tendrás que renombrar las columnas **from_station_id** y **to_station_id** en el DF de aristas, para el que además deberás seleccionar solo dichas columnas y quitar las filas repetidas ya que solo necesitamos considerar una vez cada ruta (cada pareja de estación inicial y final). Puedes almacenar el resultado del renombramiento y la eliminación de repetidos en la variable `edgesDF`.
* Una vez creado, aplica el algoritmo `pageRank` pasando como **ÚNICO** parámetro `maxIter = 5`, y **ningún parámetro más**. El algoritmo puede llegar a emplear más de 10 minutos. 
* Almacena el grafo devuelto por dicha función en la variable `pageRankGraph`, recupera el DF de sus vértices, ordénalo descendentemente en base a la columna `pagerank` y almacena el resultado en la variable `sortedPageRankGraphVerticesDF`
* Obtén el identificador de la estación más relevante (con mayor valor de la métrica pageRank, que ocupará la primera fila tras la ordenación), y almacena dicho identificador en la variable `id_mas_relevante`.
* Crea un nuevo DF de una sola fila y tres columnas llamadas `dur_media`, `dur_min` y `dur_max` con la duración **media, mínima y máxima** de los viajes de `tripsTorontoTimesDF` que **empiezan** en dicha estación (sin tener en cuenta distinción de horas o meses). **No debe usarse la función `withColumn` sino crear las columnas al vuelo con `select`**. Debe quedar almacenado en la variable `durEstMasRelevantesDF`

In [0]:
# LÍNEA EVALUABLE, NO RENOMBRAR VARIABLES
# imports necesarios.........
from graphframes import GraphFrame
# Descomentar la siguiente línea antes de lanzar pageRank:
spark.sparkContext.setCheckpointDir("/tmp")
verticesDF = None
edgesDF = None
bikeGraph = None
pageRankGraph = None
sortedPageRankGraphVerticesDF = None
id_mas_relevante = None
durEstMasRelevantesDF = None
# YOUR CODE HERE

verticesDF = tripsTorontoTimesDF.select(F.col("from_station_id").alias("id"))\
 .distinct().cache()
edgesDF = tripsTorontoTimesDF.withColumnRenamed("from_station_id", "src")\
 .withColumnRenamed("to_station_id", "dst")\
 .select("src", "dst")\
 .distinct()
bikeGraph = GraphFrame(verticesDF, edgesDF)

pageRankGraph = bikeGraph.pageRank(maxIter = 5)

sortedPageRankGraphVerticesDF = pageRankGraph.vertices.orderBy(F.col("pagerank").desc())

id_mas_relevante = sortedPageRankGraphVerticesDF.select("id").first()[0]

durEstMasRelevantesDF = tripsTorontoTimesDF.where(F.col("from_station_id") == id_mas_relevante).select(F.mean(F.col("trip_duration_seconds")).alias("dur_media"), F.min(F.col("trip_duration_seconds")).alias("dur_min"),  F.max(F.col("trip_duration_seconds")).alias("dur_max"))

durEstMasRelevantesDF.display()

dur_media dur_min dur_max 747.6957692082626 61 35130

In [0]:
assert(sortedPageRankGraphVerticesDF.head()["pagerank"] - 1.4427 < 0.01)
assert(durEstMasRelevantesDF.count() == 1)
assert(len(durEstMasRelevantesDF.columns) == 3)
rEstMasRelevantes = durEstMasRelevantesDF.head()
assert(rEstMasRelevantes.dur_min == 61)
assert(id_mas_relevante == 7060)
assert(rEstMasRelevantes.dur_media - 747.6957692082626 < 0.001)
assert(rEstMasRelevantes.dur_max == 35130)